In [1]:
import pandas as pd
#import math
#import random
#import torch
#import torch.nn as nn
#import torch.nn.functional as F
#import torch.optim as optim

In [2]:
# Importing the dataset
path1 = r'C:\\Users\\user\\.spyder-py3\\users.csv'
data = pd.read_csv(path1, sep=';' ,encoding='latin1', engine='python')
# Replace the value and its ID with another value and ID
#data.loc[data['category_id'] == 83806, 'category'] = 'Art'
#data.loc[data['category_id'] == 83806, 'category_id'] = 417240

# Save the modified data to a new CSV file
#data.to_csv(path1, index=False)



In [3]:
from sklearn.preprocessing import LabelEncoder , OneHotEncoder
y=data['Country'].values

y_labelencoder = LabelEncoder ()
y = y_labelencoder.fit_transform (y)
print (y)

X = data.loc[:, ['Age','category_id']]

X = pd.concat([X, pd.DataFrame(y, columns=['Country'])], axis=1)
print(data.isnull().sum())
print(X)

[137 116 186 ... 136  84 140]
userID            0
Gender            0
Age               0
Country           0
category          0
category_id       0
category_views    0
dtype: int64
         Age  category_id  Country
0       22.0       104958      137
1       85.0        34715      116
2       27.0        23302      186
3       85.0        57239      132
4       20.0        45026       97
...      ...          ...      ...
806755  50.0        57239      211
806756  72.0        45026      154
806757  60.0       417240      136
806758  25.0        83806       84
806759  78.0        45026      140

[806760 rows x 3 columns]


In [4]:
from sklearn.cluster import DBSCAN
from sklearn.metrics import silhouette_score, adjusted_rand_score
from sklearn import metrics

# Create DBSCAN object
dbscan = DBSCAN(eps=0.25, min_samples=15)

# Fit model and predict clusters
labels = dbscan.fit_predict(X)
# Run DBSCAN algorithm

# Count number of clusters (ignoring noise, which is labeled as -1)
n_clusters  = len(set(labels)) - (1 if -1 in labels else 0)

# Print number of clusters
print(n_clusters)
print(f"Number of clusters: {n_clusters}")


14128
Number of clusters: 14128


In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.datasets import make_blobs
from sklearn.cluster import DBSCAN
# Plot number of points in each cluster for each value of eps

#evaluation metrics
sc = metrics.silhouette_score(X, labels)
print("Silhouette Coefficient:%0.2f"%sc)
ari = adjusted_rand_score(X, labels)
print("Adjusted Rand Index: %0.2f"%ari)

In [24]:
#default figure size for matplotlib plots to be 9 inches in width and 6 inches in height.
plt.rcParams["figure.figsize"] = (9,6)

In [83]:
from surprise import SVD
import numpy as np
import surprise
from surprise import Reader, Dataset

In [58]:
#splitting shape
X

array([[-6.59633932, -7.13901457],
       [-6.13753182, -6.58081701],
       [ 5.19820575,  2.04917508],
       ...,
       [ 3.69047995,  4.60555175],
       [ 4.03036663,  1.78619838],
       [-7.44179522, -7.08933147]])

In [ ]:
train_data = X[:int(X.shape[0]*0.80)]

train_data.shape


In [ ]:
test_data=X[:int(X.shape[0]*0.80)]
test_data.shape

In [72]:
# train set from train data
# It is to specify how to read the dataframe.
# for our dataframe, we don't have to specify anything extra..

from surprise import Dataset, Reader

reader = Reader(rating_scale=(0, 5000))

# create the traindata from the dataframe...
train_data_df = pd.DataFrame(train_data, columns=['Age', 'Country','category_id'])
train_data_mf = Dataset.load_from_df(train_data_df[['Age','Country','category_id' ]], reader)
print(train_data_df)
# build the trainset from traindata.., It is of dataset format from surprise library..
trainset = train_data_mf.build_full_trainset() 

In [73]:
#test set from test data
# It is to specify how to read the dataframe.
# for our dataframe, we don't have to specify anything extra..
reader = Reader(rating_scale=(0, 5000))

# create the traindata from the dataframe...
test_data_mf = Dataset.load_from_df(test_data[['Age','Country','category_id']], reader)

# build the trainset from traindata.., It is of dataset format from surprise library..
testset = test_data_mf.build_full_trainset() 

In [100]:
svd = SVD(n_factors=100, n_epochs=20, lr_all=0.005, reg_all=0.4)

svd.fit(trainset)

In [101]:
# storing train predictions
#getting predictions of trainset
train_preds = svd.test(trainset.build_testset())

train_pred_mf = np.array([pred.est for pred in train_preds])

In [102]:
# storing test predictions
#getting predictions of trainset
test_preds = svd.test(testset.build_testset())

test_pred_mf = np.array([pred.est for pred in test_preds])

In [103]:
test_pred_mf

array([5000, 5000, 5000, ..., 5000, 5000, 5000])

In [105]:
country_values = train_data['Country'].values
for value in country_values:
    if isinstance(value, str) and not value.isdigit():
        print(value)

#Preparing train data frame
# Creating a sparse matrix
from scipy import sparse
train_sparse_matrix = sparse.csr_matrix((train_data.Age.values.astype(int),
                                         (train_data.Country.values.astype(int), train_data.category_id.values.astype(int))))


Moldova 
Lesotho 
Solomon Islands 
Mauritania 
Iraq 
Trinidad & Tobago 
Tuvalu 
Solomon Islands 
Germany 
Uruguay 
Somalia 
Tunisia 
Montserrat 
Georgia 
Cote d'Ivoire 
Jordan 
Libya 
Rwanda 
United Kingdom 
Slovakia 
Zimbabwe 
Portugal 
Zimbabwe 
Madagascar 
Botswana 
Sri Lanka 
Colombia 
Jamaica 
Gabon 
Guinea-Bissau 
Cambodia 
Luxembourg 
Chile 
Zambia 
Luxembourg 
Luxembourg 
Slovakia 
Uzbekistan 
Fiji 
Malawi 
Denmark 
Greece 
Saint Kitts & Nevis 
Tajikistan 
Philippines 
Tuvalu 
Congo, Dem. Rep. 
Japan 
Uganda 
Serbia 
Guam 
Swaziland 
Macedonia 
Bangladesh 
Togo 
Cuba 
Korea, North 
Kiribati 
Georgia 
Ethiopia 
Denmark 
Tanzania 
Kiribati 
Spain 
Jordan 
Colombia 
Equatorial Guinea 
Hong Kong 
Cyprus 
India 
Costa Rica 
Zimbabwe 
Gaza Strip 
Kiribati 
French Guiana 
Somalia 
Finland 
Antigua & Barbuda 
Syria 
Ireland 
Guernsey 
Reunion 
Cyprus 
Albania 
Egypt 
Bosnia & Herzegovina 
Dominican Republic 
Canada 
Cote d'Ivoire 
Montserrat 
Finland 
Solomon Islands 
Italy 
Jamaica 
I

Iceland 
Croatia 
Samoa 
Kazakhstan 
Georgia 
Mayotte 
Uruguay 
Benin 
Yemen 
Korea, South 
Malta 
Poland 
Dominican Republic 
Cayman Islands 
Congo, Repub. of the 
Moldova 
Sierra Leone 
Romania 
Gambia, The 
United Kingdom 
Saint Vincent and the Grenadines 
Australia 
India 
Malta 
Turkmenistan 
Armenia 
Israel 
Ireland 
Libya 
Nauru 
Turks & Caicos Is 
Belgium 
Saint Lucia 
Belgium 
Gaza Strip 
Turkmenistan 
Isle of Man 
Swaziland 
Sao Tome & Principe 
Netherlands 
Trinidad & Tobago 
Seychelles 
Guernsey 
Puerto Rico 
Gambia, The 
Bulgaria 
Saudi Arabia 
Bosnia & Herzegovina 
Estonia 
Virgin Islands 
Reunion 
Saint Kitts & Nevis 
Canada 
Belize 
Bangladesh 
Dominican Republic 
Burundi 
Vanuatu 
Congo, Repub. of the 
French Polynesia 
Spain 
Malta 
China 
Togo 
Niger 
Japan 
Saint Vincent and the Grenadines 
Micronesia, Fed. St. 
Brazil 
Serbia 
Colombia 
Netherlands Antilles 
Antigua & Barbuda 
Mali 
Jordan 
Jordan 
Netherlands 
Indonesia 
New Caledonia 
Puerto Rico 
Haiti 
Guinea 


Canada 
Swaziland 
Guyana 
China 
Cote d'Ivoire 
Macau 
Oman 
Trinidad & Tobago 
Jordan 
Paraguay 
Panama 
Libya 
Croatia 
Kenya 
Georgia 
Turkey 
Bosnia & Herzegovina 
Mongolia 
Australia 
Slovakia 
Comoros 
Fiji 
Andorra 
Anguilla 
Saint Vincent and the Grenadines 
Malaysia 
Ukraine 
Georgia 
Libya 
Iceland 
Puerto Rico 
Cambodia 
Cote d'Ivoire 
Turks & Caicos Is 
Brazil 
Korea, North 
Mauritius 
Azerbaijan 
Australia 
Mongolia 
Brunei 
St Pierre & Miquelon 
Japan 
Poland 
Estonia 
Western Sahara 
United Arab Emirates 
Tunisia 
Zambia 
India 
British Virgin Is. 
Guatemala 
Zimbabwe 
Bangladesh 
Angola 
Czech Republic 
Romania 
Israel 
Kuwait 
Iraq 
Laos 
Iran 
Trinidad & Tobago 
Macedonia 
Mauritius 
Vietnam 
Virgin Islands 
N. Mariana Islands 
Burkina Faso 
Switzerland 
Macedonia 
Vietnam 
Ghana 
New Zealand 
Gaza Strip 
Mauritania 
Togo 
Armenia 
Pakistan 
Qatar 
Finland 
Kazakhstan 
Gibraltar 
Palau 
Turks & Caicos Is 
Malawi 
Suriname 
Bolivia 
Spain 
Italy 
Indonesia 
Saint Hele

Honduras 
Ghana 
New Caledonia 
Uganda 
Central African Rep. 
American Samoa 
Gambia, The 
Tajikistan 
El Salvador 
Ecuador 
Bangladesh 
Oman 
Vietnam 
Central African Rep. 
Pakistan 
Fiji 
South Africa 
Kenya 
Bermuda 
Niger 
Cuba 
Puerto Rico 
Turkey 
Paraguay 
Indonesia 
Saudi Arabia 
Armenia 
Comoros 
Ghana 
Brazil 
Libya 
Cayman Islands 
Venezuela 
Afghanistan 
Reunion 
Benin 
Pakistan 
Virgin Islands 
Fiji 
Greenland 
Israel 
Hong Kong 
Iran 
Turks & Caicos Is 
Mozambique 
Virgin Islands 
Norway 
Namibia 
Faroe Islands 
Guinea 
Paraguay 
Aruba 
French Guiana 
New Caledonia 
Guatemala 
Cambodia 
Cook Islands 
Antigua & Barbuda 
Nicaragua 
Germany 
Kiribati 
Saudi Arabia 
Tajikistan 
Laos 
Taiwan 
Congo, Repub. of the 
Lithuania 
Turkey 
Togo 
Iraq 
San Marino 
Romania 
Mayotte 
Colombia 
Slovakia 
Djibouti 
Turkey 
Ethiopia 
Suriname 
Panama 
Turks & Caicos Is 
West Bank 
Tuvalu 
Turkmenistan 
Israel 
Paraguay 
Solomon Islands 
West Bank 
Lithuania 
United Arab Emirates 
Netherlan

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [43]:
#Preparing train data frame
# Creating a sparse matrix
from scipy import sparse
train_sparse_matrix = sparse.csr_matrix((train_data.category_views.values, (train_data.userID.values,
                                               train_data.category_id.values)))

In [44]:
# Global avg of all movies by all users
train_averages = dict()
# get the global average of ratings in our train set.
train_global_average = train_sparse_matrix.sum()/train_sparse_matrix.count_nonzero()
train_averages['global'] = train_global_average
train_averages

{'global': 631.300041112799}

In [45]:
def get_average_category_views(sparse_matrix):
    """
    Calculate the average number of category views for each category.

    Args:
        sparse_matrix: the sparse user-item matrix

    Returns:
        A dictionary with the average number of category views for each category
    """
    # Get the number of category views for each category
    category_views = sparse_matrix.sum(axis=0)

    # Get the total number of users who viewed each category
    num_users_viewed = sparse_matrix.getnnz(axis=0)

    # Calculate the average number of category views for each category
    avg_category_views = {}
    for category_id, views in enumerate(category_views.tolist()[0]):
        if num_users_viewed[category_id] > 0:
            avg_category_views[category_id] = views / num_users_viewed[category_id]

    return avg_category_views


In [51]:
#calculate the average category views for a particular category

 
# Average views given for a category
train_averages['category'] = get_average_category_views(train_sparse_matrix)
print('\nAverage views for category 11791:', train_averages['category'].get(11791))



Average views for category 11791: 116.5824884793426


In [54]:
# get categories and views from our sample train sparse matrix
_,train_category, train_views = sparse.find(train_sparse_matrix)

In [71]:
from datetime import datetime
from sklearn.metrics.pairwise import cosine_similarity

final_data = pd.DataFrame()
count = 0
for (age, category, views) in zip(data['Age'], data['category'], data['category_views']):
    start = datetime.now()
    # print(user, category)
    # --------------------- views of "category" by similar users of "user" ---------------------
    # compute the similar Users of the "user"
    user_info = [age, country.strip()]
    train_user_info = data.loc[:, ['Age', 'Country']].apply(lambda x: x.str.strip())
    user_sim = cosine_similarity([user_info], train_user_info).ravel()
    top_sim_users = user_sim.argsort()[::-1][1:]

    top_sim_users = user_sim.argsort()[::-1][1:]  # we are ignoring 'The User' from its similar users.
    # get the ratings of most similar users for this catgory
    train_views = data['category_views'].values
    top_views = train_views[top_sim_users, category]
    # we will make its length "5" by adding category averages to.
    top_sim_users_views = list(top_views[top_views != 0][:5])
    top_sim_users_views.extend([0] * (5 - len(top_sim_users_views)))
    #     print(top_sim_users_views, end=" ")
    # --------------------- views by "user"  to similar categories of "category" ---------------------
    # compute the similar categories of the "category"
    category_info = data.loc[:, ['category', 'category_views']]
    category_info = category_info[category_info['category'] != category].values
    category_sim = cosine_similarity([category_info[:, 1]], [data['category_views'].values]).ravel()
    top_sim_category = category_sim.argsort()[::-1][1:]  # we are ignoring 'The User' from its similar users.
    # get the ratings of most similar movie rated by this user..
    top_views = data.loc[:, ['category', 'category_views']].values[top_sim_category, 1]
    top_views = top_views[data.loc[:, ['category', 'category_views']].values[top_sim_category, 0] != category]
    # we will make it's length "5" by adding user averages to.
    top_sim_category_views = list(top_views[top_views != 0][:5])
    top_sim_category_views.extend([0] * (5 - len(top_sim_category_views)))
    #     print(top_sim_categories_views, end=" : -- ")

    # -----------------prepare the row to be stores in a file-----------------#
    row = list()
    row.append(age)
    row.append(category)
    # add category views to this data
    row.append(views)

AttributeError: Can only use .str accessor with string values!

In [25]:
final_data.columns=['user', 'category', 'GAvg', 'sur1', 'sur2', 'sur3', 'sur4', 'sur5',
            'smr1', 'smr2', 'smr3', 'smr4', 'smr5', 'UAvg', 'MAvg', 'category_views']

NameError: name 'final_data' is not defined

In [107]:
final_data.shape

(421280, 16)

In [108]:
final_data.head()

user  category        GAvg   sur1   sur2   sur3   sur4   sur5     smr1  \
0  12470     11791  631.300041   76.2   76.2   76.2   76.2   76.2  2234.56   
1  12471     11791  631.300041  152.4  152.4  152.4  152.4  152.4  4469.12   
2  12473     11791  631.300041   76.2   76.2   76.2   76.2   76.2   796.64   
3  12474     11791  631.300041   76.2   76.2   76.2   76.2   76.2   398.32   
4  12476     11791  631.300041   76.2   76.2   76.2   76.2   76.2  4469.12   

      smr2    smr3      smr4       smr5         UAvg        MAvg  \
0   398.32  129.00  222.8000   224.6000   426.108750  116.582488   
1   796.64  258.00  445.6000  1239.5920  1239.592000  116.582488   
2   387.00   11.70  111.6900   276.6460   276.646000  116.582488   
3   387.00  111.69  243.3025   243.3025   243.302500  116.582488   
4  1194.96  222.80  112.3000   223.3800  1049.793333  116.582488   

   category_views  
0            76.2  
1           228.6  
2            76.2  
3            76.2  
4            76.2

In [24]:
final_data['mf_svd']=train_pred_mf

NameError: name 'final_data' is not defined

In [5]:
# create a dataframe with the predictions
mf_pred_df = pd.DataFrame({'mf_svd': train_pred_mf})

# check if the indices match
assert mf_pred_df.index.equals(final_data.index), "Indices do not match!"

# concatenate the dataframes
final_data = pd.concat([final_data, mf_pred_df], axis=1)


NameError: name 'train_pred_mf' is not defined